# Automatic catchment delineation using Python and Postgis

In [1]:
#Loading required modules

import os
import shutil
import subprocess
from subprocess import Popen, PIPE, CalledProcessError
import psycopg2 as db
import psycopg2.extras
from psycopg2 import sql
from psycopg2.extensions import AsIs
from encrypt import decryptCredentials,decryptString
from procedures import refreshProcedures
import yaml
import getpass

from pygments import highlight
from pygments.formatters import HtmlFormatter
from pygments.lexers import YamlLexer
from pygments.lexers.python import Python3Lexer
from pygments.lexers.shell import BashLexer
from IPython.core.display import display,HTML

import json
import gmaps
import gmaps.geojson_geometries
import geojson

#Starting server with geodatabase
with Popen(['gcloud', 'compute', 'instances', 'start', 'geonorway-dtm10', '--zone=europe-west2-a'],
           stdout=PIPE, bufsize=1, universal_newlines=True) as p:
    for line in p.stdout:
        if line != NoneType:
            print(line, end='') 
    if p.returncode != 0 and p.returncode != None:
        raise CalledProcessError(p.returncode, p.args)
        
    p.wait()

## Pre-requisites

The PostgreSQL database is hosted on google cloud and has the url http://catchment.niva.no

The database name is _geonorway_, which is where data will be stored.

Both rivers and dems can be uploaded to the database to dynamically generated tables using code in this notebook.
This should only be done once since it is a time-consuming operation.

For future reference, these are some of the commands used to create the database:
```

cursor.execute('ALTER DATABASE \"Basins_HWI\" SET search_path=public, postgis, contrib,topology;')
cursor.execute('ALTER DATABASE \"Basins_HWI\" SET postgis.gdal_enabled_drivers = \'ENABLE_ALL\';')
cursor.execute('CREATE EXTENSION postgis;')
cursor.execute('CREATE EXTENSION postgis_topology;')
cursor.execute('ALTER DATABASE \"Basins_HWI\" SET search_path=public, postgis, contrib,topology;')
cursor.execute('ALTER DATABA \"Basins_HWI\" SET postgis.gdal_enabled_drivers = \'ENABLE_ALL\';')
cursor.execute('SELECT pg_reload_conf();')
cursor.execute('SET postgis.enable_outdb_rasters TO True;')
```

The operations required to organize the elevation and river data datasets necessary to perform the catchment delineation have been (partially) stored in the geodatabase as stored procedures. These stored procedures are defined in the _procedures.py_ file in this repository.


### Elevation data

Elevation data can be automatically downloaded from Kartverket using the following script:

In [2]:
downloadScript = 'loadDemFromKartverket.py'
fid = open(downloadScript,'r')
code = fid.read()
fid.close
result = highlight(code, Python3Lexer(),HtmlFormatter(linenos=False))
display(HTML("""
<style>
{pygments_css}
</style>
""".format(pygments_css=HtmlFormatter().get_style_defs('.highlight'))))
display(HTML(result))

#The fab file, with the settings needed to interact with the remote machine are in fabfile.py in 
#the current directory
#Running loading script on remote machine. This can take a long time, depending on data size.
loadDEM=False
if loadDEM:
    remotePath='/home/jose-luis/dem'
    #Connecting to remote machine using ssh
    #This will download the data from Kartverket in the remote machine to the specified remotePath
    #It first copies the python script and then executes it
    with Popen(['fab', 'loadDEM:{},{}'.format(remotePath,downloadScript)], stdout=PIPE, bufsize=1, universal_newlines=True) as p:
        for line in p.stdout:
            print(line, end='') # process line here

    if p.returncode != 0:
        raise CalledProcessError(p.returncode, p.args)
        
    p.wait()

### River shapefiles

The river shapefiles was downloaded from NVE and uploaded geodatabase to _norway_ in a table called _norway.rivers_ .

### Postgis database

Postgresql 9.6.6 with Postgis 3.5.1 have been used.
Postgis might need to be explicitly enabled.
Setting up the database server is beyond the scope of this document.

The minimum commands to install the database:
**sudo apt-get install postgresql postgresql-client postgresql-contrib postgresql-server-dev-all**

Note that if you want to use handle stored procedures through a shell, then you need to instal [plsh](https://github.com/petere/plsh.git).

#### Connection credentials

The credentials necessary to connect to the database have been encrypted using the _cryptography_ package.
The encryption and decryption functions are defined in the _encrypt.py_ file of this repository.

### Taudem

The catchment delineation routines come from the [Taudem](http://hydrology.usu.edu/taudem/taudem5/index.html) package. The package's routines should be installed and available from the path.
Please not that it might be necessary to checkout the master branch (the default clone is a development branch) in order to get Taudem to compile

### GDAL 

Some GDAL tools need to be installed for Taudem to compile and also to move data to/from the database.
In Linux, the following commands should be sufficient.

**sudo apt-get install gdal-bin libgdal-dev python3-gdal**

## Catchment delineation

### Setting up credentials and connecting to database

In [4]:
#Setting up credentials for database access. These should have been previously encrypted
token = b'gAAAAABayyyn8ZnEstm8ZQqClUYQ-IqFFuMO4QTbmFJADHWBAcirh52s5stDwSwtVK7qVm5tzdTNFxTQjuRF28b1t2rosFSl_nnTowWrD4itOjkzF7s6Kg_qa1Adqpj59OAfBapgkToUQUHvEFY1Njc4he36AC76gmb8t0CJCq4ze2pDHWIlGdDacZxQ1jq14uLVxrFfCTSxDPX8Mx9W1av723etkOdWvw=='
key = getpass.getpass('Password: ')
credentials = decryptCredentials(token,key)

#Setting up credentials for google maps api access
apiToken = b'gAAAAABaXyLsGnF3ms4sC3ZhoLCwWAx9q0tydWl8XKEwOy8CO0W6Eqc8J4om8HNDlNR9nExYCmSrelp8W5R-PLtcce1I2UgW3YnlXXqWvrMN-outYwXhZoc59djfF752mzOPqXBHgpNC'
apiKey = decryptString(apiToken,key)
gmaps.configure(api_key=apiKey)

# Testing connection to database
try : 
    conn = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],credentials['username'],credentials['host'],credentials['password']))
except :
    print("Unable to connect")
    
conn.close()
    

Password: ········


### Refreshing stored procedures

This is necessary if the procedures defined in _procedures.py_ are modified.

In [5]:
# Refreshing stored procedures if necessary.
# Need to be a superuser in order to refresh stored procedures.
refresh = True
if refresh :
    #This will only work if user postgres has the same password as "credentials" user. Otherwise, this needs
    #to be passed explicitly
    refreshProcedures(credentials['database'],'postgres',credentials['host'],credentials['password'])
    try : 
        tempConn = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],'postgres',credentials['host'],credentials['password']))
    except :
        print("Unable to connect")
    tempCursor = tempConn.cursor()
    tempCursor.execute('''ALTER SCHEMA procedures OWNER TO %s; ''', ( AsIs ( '"' + credentials['username'] + '"' ) ,))
    tempCursor.execute('''ALTER FUNCTION procedures.loadRivers(text,integer,text,text,text,text,text) OWNER TO %s; ''', ( AsIs ( '"' + credentials['username'] + '"' ) ,))
    tempCursor.execute('''ALTER FUNCTION procedures.initializeSchema(text) OWNER TO %s; ''', ( AsIs ( '"' + credentials['username'] + '"' ) ,))
    tempConn.commit()
    tempConn.close()

### Storing rivers in database

This is time consuming but only needs to run during the first setup.

In [5]:
# Adding shapefile containing all of Norway's rivers    
#Shapefile info and schema.table where they will be stored

addRivers = False
#Please note that this should be the local path in the database server
riversShp = '/home/jose_luis_guerrero/NVEData/Elv/Elv_Elvenett_3035.shp'
epsg_num = 3035 
schema = 'norway'
table = 'rivers'

if addRivers:
# Connecting as user specified in credentials
    connection = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],
                                                                           credentials['username'],
                                                                           credentials['host'],
                                                                           credentials['password']))
#And a test query
    cursor = connection.cursor()

#Creating schema to store shapefiles

    cursor.execute('''SELECT procedures.initializeSchema(%s)''',(schema,))
    connection.commit()
    cursor.execute('''SELECT procedures.loadRivers(%s,%s,%s,%s,%s,%s,%s);''', (riversShp, epsg_num, schema, table,
                                                             credentials['password'],
                                                             credentials['database'],
                                                             credentials['username']))
    connection.commit()
    for i in cursor :
        print(i)
    



### Processing DTM using Taudem

The DTM data was downloaded using the script shown in the "Elevation Data" section above.
The downloaded data are then:

* Tiled as .vrt raster
* vrt raster is stored as .tif (warped to a common projection if necessary)
* resampled to reduce the resolution
* The tif is processed with Taudem

The commands will be executed in the server using fabric. The commands are defined in _fabfile.py_.

In [10]:
quote psqlburnRivers=False
if burnRivers:
    remotePath='/home/jose-luis/dem'
    #Executing commands in the remote server
    print(remotePath, riversShp)
    with Popen(['fab', 'preprocessDEM:{},{},{},{},{}'.format(remotePath,
                                                             'Elv_Elvenett_3035',
                                                             riversShp,
                                                             '25',
                                                             '25' )
               ], stdout=PIPE, bufsize=1, universal_newlines=True) as p:
        for line in p.stdout:
            print(line, end='') 

    if p.returncode not in (0,None) :
        raise CalledProcessError(p.returncode, p.args)
        
    p.wait()

/home/jose-luis/dem /home/jose_luis_guerrero/NVEData/Elv/Elv_Elvenett_3035.shp
[catchment.niva.no] Executing task 'preprocessDEM'
I'm alive
[catchment.niva.no] Executing task 'buildVrt'
[catchment.niva.no] run: cd /home/jose-luis/dem/data && rm -f norway* && gdalbuildvrt norway.vrt *.tif
[catchment.niva.no] out: 0...10...20...30...40...50...60...70...80...90...100 - done.
[catchment.niva.no] out: 

[catchment.niva.no] Executing task 'transformVrt'
[catchment.niva.no] run: cd /home/jose-luis/dem/data && gdal_translate norway.vrt norway.tif
[catchment.niva.no] out: Input file size is 123711, 153441
[catchment.niva.no] out: 0...10...20...30...40...50...60...70...80...90...100 - done.
[catchment.niva.no] out: 

[catchment.niva.no] Executing task 'resampleRast'
[catchment.niva.no] run: cd /home/jose-luis/dem/data && gdalwarp -overwrite -s_srs EPSG:3045 -t_srs EPSG:3035 -tr 25 25 -r cubicspline norway.tif norway_resampled.tif
[catchment.niva.no] out: Creating output file that is 54381P x 641

And the raster with the burned rivers can now be processed with Taudem. The script's lone requirement is the DEM with burned-in rivers.

In order have more computing power, will we run the catchment processing in a computer with 96 cores.

In [6]:
with Popen(['gcloud', 'compute', 'instances', 'start', 'expensive', '--zone=northamerica-northeast1-b'],
           stdout=PIPE, bufsize=1, universal_newlines=True) as p:
    for line in p.stdout:
        if line != NoneType:
            print(line, end='') 
    if p.returncode != 0 and p.returncode != None:
        raise CalledProcessError(p.returncode, p.args)
        
    p.wait()

#Getting IP of "expensive"
process = subprocess.Popen(["gcloud compute instances list | grep expensive | awk '{print $5}'"],
                          shell=True,
                          stdout=subprocess.PIPE,
                          stderr=subprocess.PIPE)
ip, err = process.communicate()
expensive_ip =str(ip,'utf-8')
print("The ip of the 'expensive' remote host is {}".format(expensive_ip))


The ip of the 'expensive' remote host is 35.203.18.27



In [7]:
#Copying DEM to "expensive"
file_to_copy = 'norway_burned_rivers.tif'
with Popen(['fab', 'backpublish:{},{},{},{}'.format('stage',
                                                 'production',
                                                  file_to_copy,
                                                  expensive_ip
                                                  )
           ], stdout=PIPE, bufsize=1, universal_newlines=True) as p:
    for line in p.stdout:
        print(line, end='') 

    if p.returncode != ( 0 or None ):
        raise subprocess.CalledProcessError(p.returncode, p.args)
        
    p.wait()

So now a server with 96 cores is running.
The file with the burned rivers will be copied and used as a base for the hydrological processing.

In [6]:
num_processors=96

with Popen(['fab', 'hydrology:{},{},{}'.format(file_to_copy,
                                               num_processors,
                                               expensive_ip
                                              ),
           ],
           stdout=PIPE, bufsize=1, universal_newlines=True) as p:
    for line in p.stdout:
        print(line, end='') 
    if p.returncode != 0 and p.returncode != None:
        raise subprocess.CalledProcessError(p.returncode, p.args)
        
    p.wait()

[catchment.niva.no] Executing task 'hydrology'
[35.203.46.48] Executing task 'pitremove'
[35.203.46.48] run: cd data && mpiexec -n 96 pitremove -z norway_burned_rivers.tif -fel fel.tif
[35.203.46.48] out: PitRemove version 5.3.8
[35.203.46.48] out: Input file norway_burned_rivers.tif has projected coordinate system.
[35.203.46.48] out: This run may take on the order of 9 minutes to complete.
[35.203.46.48] out: This estimate is very approximate. 
[35.203.46.48] out: Run time is highly uncertain as it depends on the complexity of the input data 
[35.203.46.48] out: and speed and memory of the computer. This estimate is based on our testing on 
[35.203.46.48] out: a dual quad core Dell Xeon E5405 2.0GHz PC with 16GB RAM.
[35.203.46.48] out: Setting BIGTIFF, File: fel.tif, Anticipated size (GB):12.15
[35.203.46.48] out: Processes: 96
[35.203.46.48] out: Header read time: 5.884958
[35.203.46.48] out: Data read time: 5.203347
[35.203.46.48] out: Compute time: 72.351444
[35.203.46.48] out: W

[35.203.46.48] out: ....................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

And now getting the processed data back to the geodatabase

In [9]:
with Popen(['fab', 'getHydroData:{},{}'.format( ['fel.tif', 'flow_dir.tif', 'flow_acc.tif'],
                                                   expensive_ip
                                                 ),
           ],
           stdout=PIPE, bufsize=1, universal_newlines=True) as p:
    for line in p.stdout:
        print(line, end='') 
    if p.returncode != 0 and p.returncode != None:
        raise subprocess.CalledProcessError(p.returncode, p.args)
        
    p.wait()

In [10]:
#Stopping the expensive server
with Popen(['gcloud', 'compute', 'instances', 'stop', 'expensive' '--zone=northamerica-northeast1-b'],
           stdout=PIPE, bufsize=1, universal_newlines=True) as p:
    for line in p.stdout:
        print(line, end='') 
    if p.returncode != 0 and p.returncode != None:
        raise subprocess.CalledProcessError(p.returncode, p.args)
        
    p.wait()

### Adding the elevation, filled elevation, flow direction and flow accumulation rasters to the geodatabase

In [5]:
#['norway_resampled.tif', 'fel.tif', 'flow_dir.tif', 'flow_acc.tif']
with Popen(['fab', 'loadDEMToDB:{},{},{},{},{}'.format( 'flow_dir.tif',
                                                     credentials['database'],
                                                     credentials['username'],
                                                     credentials['host'],
                                                     credentials['password']                                                    
                                                   ),
                                                     
           ],
           stdout=PIPE, bufsize=1, universal_newlines=True) as p:
    for line in p.stdout:
        print(line, end='') 
    if p.returncode != 0 and p.returncode != None:
        raise subprocess.CalledProcessError(p.returncode, p.args)
        
    p.wait()

[catchment.niva.no] Executing task 'loadDEMToDB'
flow_dir.tif
flow_dir.tif
[catchment.niva.no] Executing task 'loadDEMs'
[catchment.niva.no] run: raster2pgsql -I -C -M -b 1 -r -s 3035 -d -t auto -l 2,4,8,16,32,64 dem/data/flow_dir.tif norway.flow_dir | PGPASSWORD=kakaroto psql -U jose-luis -d geonorway -h localhost -p 5432 -q
[catchment.niva.no] out: Processing 1/1: dem/data/flow_dir.tif
[catchment.niva.no] out: INFO: Using computed tile size: 89x77
[catchment.niva.no] out: NOTICE:  table "flow_dir" does not exist, skipping
[catchment.niva.no] out: NOTICE:  table "o_2_flow_dir" does not exist, skipping
[catchment.niva.no] out: NOTICE:  table "o_4_flow_dir" does not exist, skipping
[catchment.niva.no] out: NOTICE:  table "o_8_flow_dir" does not exist, skipping
[catchment.niva.no] out: NOTICE:  table "o_16_flow_dir" does not exist, skipping
[catchment.niva.no] out: NOTICE:  table "o_32_flow_dir" does not exist, skipping
[catchment.niva.no] out: NOTICE:  table "o_64_flow_dir" does not exi

[catchment.niva.no] out:  addoverviewconstraints 
[catchment.niva.no] out: ------------------------
[catchment.niva.no] out:  t
[catchment.niva.no] out: (1 row)
[catchment.niva.no] out: 
[catchment.niva.no] out:  addoverviewconstraints 
[catchment.niva.no] out: ------------------------
[catchment.niva.no] out:  t
[catchment.niva.no] out: (1 row)
[catchment.niva.no] out: 
[catchment.niva.no] out:  addoverviewconstraints 
[catchment.niva.no] out: ------------------------
[catchment.niva.no] out:  t
[catchment.niva.no] out: (1 row)
[catchment.niva.no] out: 
[catchment.niva.no] out:  addoverviewconstraints 
[catchment.niva.no] out: ------------------------
[catchment.niva.no] out:  t
[catchment.niva.no] out: (1 row)
[catchment.niva.no] out: 
[catchment.niva.no] out:  addoverviewconstraints 
[catchment.niva.no] out: ------------------------
[catchment.niva.no] out:  t
[catchment.niva.no] out: (1 row)
[catchment.niva.no] out: 
[catchment.niva.no] out:  addoverviewconstraints 
[catchment.niva

Adding extent to uploaded elevation rasters. This will make computations faster down the line.

In [6]:
#Adding extent column to uploaded rasters
conn = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],
                                                                       credentials['username'],
                                                                        credentials['host'],
                                                                        credentials['password']
                                                                      )
                       )

cursor = conn.cursor()

cursor.execute("SELECT procedures.setExtentTable(%s,%s);",('norway','fel'))
conn.commit()
cursor.execute("SELECT procedures.setExtentTable(%s,%s);",('norway','flow_acc'))
conn.commit()
cursor.execute("SELECT procedures.setExtentTable(%s,%s);",('norway','flow_dir'))
conn.commit()

conn.close()

### Setting outlets for catchment delineation
As many catchment as there are outlets will be delineated. The outlets should be given in _.yaml_ file with the following format:



In [6]:
stationsFile = 'stations.yaml'

fid = open(stationsFile,'r')
code = fid.read()
fid.close
result = highlight(code, YamlLexer(),HtmlFormatter(linenos=False))
display(HTML("""
<style>
{pygments_css}
</style>
""".format(pygments_css=HtmlFormatter().get_style_defs('.highlight'))))
display(HTML(result))

The _.yaml_ file will be read and the above data stored as a table containing point geometries.

In [7]:
#Adding stations (coordinates) where the basins will be delineated

# Connecting as user specified in credentials
conn = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],
                                                                       credentials['username'],
                                                                        credentials['host'],
                                                                        credentials['password']
                                                                      )
                       )
#And a test query
cursor = conn.cursor()

#Reading station data from a yaml file
stations = yaml.load(open(stationsFile))  
db.extras.register_composite('station_info',cursor)

#Re-arranging data as a list of tuples and passing it to pg with the help
#of pyscopg2 extras
allStations = list()
for i in stations:
    i=i['station']
    data = ( i['station_name'],
             i['station_id'],
             i['longitude'],
             i['latitude'],
             i['buffer'],
             i['epsg']
           )
    allStations.append(data)

cursor.execute("SELECT procedures.initializeStations();")
conn.commit()

cursor.execute("SELECT procedures.addStations( %s::station_info[] );",(allStations,))
conn.commit()



### Gathering data for catchment delineation
#### Initializing schema to store results

In [8]:
resultsSchema = 'basins'
cursor.execute("SELECT procedures.initializeResultsSchema( %s );",(resultsSchema,))
conn.commit()

#### Gathering dem from a circular buffer around the station

The Norway dem will be queried to get a the elevation in a circular buffer around the station. The size (radius) of the buffer is defined in the _.yaml_ file.

The rivers shapefile will be clipped according to the extent of the buffered dem and burned into it prior to catchment delineation.

The actual coordinates of the station will be modified so they fall on a river. The outlet will be set as the closest point between station coordinates and the rivers shapefile.

Please note that both rivers, dems, and stations might come in different coordinate systems. This is automatically handled only for some projections.

All the base data will be stored in a table.

In [9]:
# Getting raster around station

#Creating table to store results
dataTable = 'dem'
print('Creating base data...')
cursor.execute(" SELECT procedures.createDataTable(%s,%s);", (resultsSchema,dataTable))
conn.commit()
print('Done!')

Creating base data...
Done!


### Catchment delineation

Currently the results will be stored for each different available dem projection and the table names generated dynamically based on the projection's epsg number.

In [10]:
#Creating tables to store results. One table per dem projection
resultsTable = 'results'
cursor.execute("SELECT procedures.createResultsTable(%s,%s);",(resultsSchema,resultsTable));
conn.commit()

Preparing 
* _Taudem_ statements
* *gdal_translate* statements to get raster from database as _.tif_. This will be an input to taudem.
* _pgsql2psql_ to get each outlet as a shapefile that will be used to delineate the catchment by taudem.
* _raster2pgsql_ to upload the watershed raster to the results table. The catchment is delineated from this dem. 

In [11]:
with Popen(['fab', 'processBasin:{},{},{},{},{},{},{},{}'.format(
                                                 credentials['username'],
                                                 credentials['password'],
                                                 credentials['database'],
                                                 resultsSchema,
                                                 dataTable,
                                                 'flow_dir',
                                                 'outlet',
                                                 '/home/jose-luis/Trash/' 
                                                 )
           ], stdout=PIPE, bufsize=1, universal_newlines=True) as p:
        for line in p.stdout:
            print(line, end='') 

        if p.returncode != ( 0 or None ):
            raise subprocess.CalledProcessError(p.returncode, p.args)
        
        p.wait()
print("Done!")

[catchment.niva.no] Executing task 'processBasin'
[catchment.niva.no] Executing task 'createTmpDir'
[catchment.niva.no] run: rm -rf /home/jose-luis/Trash/ && mkdir /home/jose-luis/Trash/ && cd /home/jose-luis/Trash/ && chmod a+w /home/jose-luis/Trash/
[catchment.niva.no] Executing task 'getStationIdList'
[catchment.niva.no] run: echo "\copy (SELECT station_id FROM basins.dem) TO '/home/jose-luis/Trash/stations.csv' (format csv);" | psql -d geonorway
[catchment.niva.no] out: COPY 6
[catchment.niva.no] out: 

[catchment.niva.no] Executing task 'generateRast'
[catchment.niva.no] run:  echo "SELECT procedures.dumpAsTif('basins','dem','flow_dir','/home/jose-luis/Trash/');" | PGPASSWORD=kakaroto psql -d geonorway -h localhost -U postgres         
[catchment.niva.no] out: NOTICE:  table "binary" does not exist, skipping
[catchment.niva.no] out:  dumpastif 
[catchment.niva.no] out: -----------
[catchment.niva.no] out:  
[catchment.niva.no] out: (1 row)
[catchment.niva.no] out: 
[catchment.niva

[catchment.niva.no] out: INSERT 0 1
[catchment.niva.no] out: COMMIT
[catchment.niva.no] out: INSERT 0 1
[catchment.niva.no] out: DROP TABLE
[catchment.niva.no] out: SELECT a.station_name, a.station_id, a.outlet FROM basins.dem AS a WHERE a.station_id=108
[catchment.niva.no] out: Initializing... 
[catchment.niva.no] out: Done (postgis major version: 2).
[catchment.niva.no] out: Output shape: Point
[catchment.niva.no] out: Dumping: X [1 rows].
[catchment.niva.no] out: Gage Watershed version 5.3.8
[catchment.niva.no] out: Input file flow_dir108.tif has projected coordinate system.
[catchment.niva.no] out: This run may take on the order of 1 minutes to complete.
[catchment.niva.no] out: This estimate is very approximate. 
[catchment.niva.no] out: Run time is highly uncertain as it depends on the complexity of the input data 
[catchment.niva.no] out: and speed and memory of the computer. This estimate is based on our testing on 
[catchment.niva.no] out: a dual quad core Dell Xeon E5405 2.0G

### Visualization

The catchments will be displayed in google maps.


In [13]:
conn = db.connect("dbname={} user={} host={} password={}".format(credentials['database'],
                                                                       credentials['username'],
                                                                        credentials['host'],
                                                                        credentials['password']
                                                                      )
                       )
#And a test query
cursor = conn.cursor()
cursor.execute(''' SELECT json_build_object(
                    'type', 'FeatureCollection',

                    'features', json_agg(
                        json_build_object(
                            'type',       'Feature',
                            'label',       station_name,
                            'geometry',   ST_AsGeoJSON(ST_ForceRHR(st_transform(basin,4326)))::json,
                            'properties', jsonb_set(row_to_json(results)::jsonb,'{basin}','0',false)
                             )
                        )
                   )
                    FROM basins.results;  '''
              )
layer=cursor.fetchone()[0]

fig = gmaps.figure()

basin_layer = gmaps.geojson_layer(layer)
fig.add_layer(basin_layer)
    
    
cursor.execute('''SELECT a.station_name, st_x(st_transform(a.outlet,4326)),
                  st_y(st_transform(a.outlet,4326)), st_area(b.basin)
                  FROM basins.dem AS a
                  INNER JOIN basins.results AS b 
                  ON a.station_id = b.station_id;''')  

rows=cursor.fetchall()

outlets = []
for row in rows:
    print(row)
    currentDict = {"name" : row[0], "location": (row[2],row[1]), "area": row[3]/1000000}
    outlets.append(currentDict)

outlet_locations = [outlet["location"] for outlet in outlets]
info_box_template = """
<dl>
<dt>Name</dt><dd>{name}</dd>
<dt>Area</dt><dd>{area} km<sup>2</sup></dd>
</dl>
"""                                                
outlet_info = [info_box_template.format(**outlet) for outlet in outlets]                                                 
marker_layer = gmaps.marker_layer(outlet_locations, info_box_content=outlet_info)
fig.add_layer(marker_layer)


fig


('Birkenes', 8.2416482166719, 58.385461205931, 435000.0)
('Øygardsbekken', 6.10640063214898, 58.6219112754872, 2363750.0)
('Storgama v. dam', 8.65370012981789, 59.0523165033965, 4375.0)
('Kårvatn', 8.89355714536466, 62.7828336703377, 24330000.0)
('Dalelv', 30.3855851997138, 69.6846698910753, 3089375.0)
('Langtjern, utløp', 9.72672739752392, 60.3724668497833, 4755625.0)


Figure(layout=FigureLayout(height='420px'))

In [11]:
conn.close()